# 텐서플로를 이용한 데이터 적재와 전처리
메모리 용량에 맞지 않는 아주 큰 규모의 데이터셋으로 딥러닝 시스템을 학습해야 하는 경우가 많음.  
텐서플로는 **데이터 API**를 이용해 대규모 데이터셋을 효율적으로 로드하고 전처리하기 쉽다.  
> **데이터셋 객체를 만들고 데이터를 읽어 올 위치와 변환 방법을 지정하면 됨.**  
멀티스레딩, 큐, 배치, 프리페치같은 상세한 사항을 모두 대신 처리해준다고 함

기본 기능으로 데이터 API는  
- 텍스트파일(csv 파일)
- 고정 길이의 레코드를 가진 이진 파일
- 텐서플로의 **TFRecord** 포맷을 사용하는 이진 파일

에서 데이터를 읽을 수 있음.

대용량 데이터를 효율적으로 읽는 것은 어렵기만 할 뿐 아니라 정규화같은 **데이터 전처리**가 필요함.  
수치형 필드뿐 아니라 텍스트, 범주형 특성 등도 있음. 이런 특성들은 **원-핫 인코딩, BoW 인코딩, 임베딩** 등을 사용하여 인고딩해야 함.  
> 이런 모든 전처리 과정을 처리하기 위해 **사용자 정의 전처리 층** 을 만드는 방법이 있음.  
아니면 케라스에서 제공하는 **표준 전처리 층** 을 사용할 수도 있음.

이 장에서는  
- **데이터 API**
- **TFRecord** 포맷
- **사용자 전처리 층을 만드는 방법**
- **케라스 전처리 층을 사용하는 방법**

을 다룸.

---
# 데이터 API
데이터 API의 중심에는 **데이터셋** 개념이 있다고 함. 이는 연속된 데이터 샘플을 나타냄.

In [1]:
import tensorflow as tf
from tensorflow import keras

In [2]:
X = tf.range(10)
dataset = tf.data.Dataset.from_tensor_slices(X)
dataset

<TensorSliceDataset shapes: (), types: tf.int32>

>**from_tensor_slices()** 함수는 텐서를 받아 (첫 번째 차원을 따라: 배치 사이즈?) X의 각 원소가 아이템으로 표현되는 **tf.data.Dataset**을 만듦.  

즉 이 데이터셋은 텐서 0, 1, 2, ... 9에 해당하는 10개의 아이템을 가짐.  
이 경우 tf.data.Dataset.range(10)으로 만든 데이터셋과 동일

In [3]:
for item in dataset:
    print(item)

tf.Tensor(0, shape=(), dtype=int32)
tf.Tensor(1, shape=(), dtype=int32)
tf.Tensor(2, shape=(), dtype=int32)
tf.Tensor(3, shape=(), dtype=int32)
tf.Tensor(4, shape=(), dtype=int32)
tf.Tensor(5, shape=(), dtype=int32)
tf.Tensor(6, shape=(), dtype=int32)
tf.Tensor(7, shape=(), dtype=int32)
tf.Tensor(8, shape=(), dtype=int32)
tf.Tensor(9, shape=(), dtype=int32)


해당 데이터셋의 아이템을 순회하는 예시

---
## 연쇄 변환
데이터셋이 준비되면 **변환 메서드**를 호출하여 여러 종류의 변환을 수행할 수 있음.  
각 메서드는 새로운 데이터셋을 반환하므로 다음과 같이 변환 메서드를 연결할 수 있음.

In [4]:
dataset = tf.data.Dataset.from_tensor_slices(X)
dataset = dataset.repeat(3).batch(7)
for item in dataset:
    print(item)

tf.Tensor([0 1 2 3 4 5 6], shape=(7,), dtype=int32)
tf.Tensor([7 8 9 0 1 2 3], shape=(7,), dtype=int32)
tf.Tensor([4 5 6 7 8 9 0], shape=(7,), dtype=int32)
tf.Tensor([1 2 3 4 5 6 7], shape=(7,), dtype=int32)
tf.Tensor([8 9], shape=(2,), dtype=int32)


>**repeat()** 메서드는 해당 데이터셋을 매개변수(정수)만큼 반복함. 매개변수가 없으면 끊임없이 반복  
>**batch()** 메서드는 매개변수(정수)만큼 끊어서 데이터셋을 반환함. *drop_remainder=True* 로 설정하면 길이가 모자란 마지막 배치를 버림.

In [5]:
dataset = tf.data.Dataset.from_tensor_slices(X)
dataset = dataset.repeat(3).batch(7, drop_remainder=True)
for item in dataset:
    print(item)

tf.Tensor([0 1 2 3 4 5 6], shape=(7,), dtype=int32)
tf.Tensor([7 8 9 0 1 2 3], shape=(7,), dtype=int32)
tf.Tensor([4 5 6 7 8 9 0], shape=(7,), dtype=int32)
tf.Tensor([1 2 3 4 5 6 7], shape=(7,), dtype=int32)


> 주의할 점은 데이터셋의 메서드가 데이터셋을 바꾸는게 아니라 **새로운 데이터셋을 만드는 것임**  
따라서 꼭 새로운 데이터셋을 반환받아야 함. 안그러면 날라감

In [6]:
dataset = tf.data.Dataset.from_tensor_slices(X)
dataset = dataset.repeat(3).batch(7, drop_remainder=True)
dataset = dataset.map(lambda x: x*2)
for item in dataset:
    print(item)

tf.Tensor([ 0  2  4  6  8 10 12], shape=(7,), dtype=int32)
tf.Tensor([14 16 18  0  2  4  6], shape=(7,), dtype=int32)
tf.Tensor([ 8 10 12 14 16 18  0], shape=(7,), dtype=int32)
tf.Tensor([ 2  4  6  8 10 12 14], shape=(7,), dtype=int32)


> **map()** 메서드를 호출하여 **아이템을 변환**할 수도 있음.  
이 함수를 데이터에 원하는 어떤 **전처리 작업**에도 적용할 수 있음.  
이때 메서드에 전달하는 함수는 텐서플로 함수로 변환 가능해야 함.

In [7]:
dataset = tf.data.Dataset.from_tensor_slices(X)
dataset = dataset.repeat(3).batch(7, drop_remainder=True)
dataset = dataset.apply(tf.data.experimental.unbatch())
for item in dataset:
    print(item)

Instructions for updating:
Use `tf.data.Dataset.unbatch()`.
tf.Tensor(0, shape=(), dtype=int32)
tf.Tensor(1, shape=(), dtype=int32)
tf.Tensor(2, shape=(), dtype=int32)
tf.Tensor(3, shape=(), dtype=int32)
tf.Tensor(4, shape=(), dtype=int32)
tf.Tensor(5, shape=(), dtype=int32)
tf.Tensor(6, shape=(), dtype=int32)
tf.Tensor(7, shape=(), dtype=int32)
tf.Tensor(8, shape=(), dtype=int32)
tf.Tensor(9, shape=(), dtype=int32)
tf.Tensor(0, shape=(), dtype=int32)
tf.Tensor(1, shape=(), dtype=int32)
tf.Tensor(2, shape=(), dtype=int32)
tf.Tensor(3, shape=(), dtype=int32)
tf.Tensor(4, shape=(), dtype=int32)
tf.Tensor(5, shape=(), dtype=int32)
tf.Tensor(6, shape=(), dtype=int32)
tf.Tensor(7, shape=(), dtype=int32)
tf.Tensor(8, shape=(), dtype=int32)
tf.Tensor(9, shape=(), dtype=int32)
tf.Tensor(0, shape=(), dtype=int32)
tf.Tensor(1, shape=(), dtype=int32)
tf.Tensor(2, shape=(), dtype=int32)
tf.Tensor(3, shape=(), dtype=int32)
tf.Tensor(4, shape=(), dtype=int32)
tf.Tensor(5, shape=(), dtype=int32)
tf.T

> **apply** 메서드는 **데이터셋 전체에 변환을 적용**함.  

In [8]:
dataset = tf.data.Dataset.from_tensor_slices(X)
dataset = dataset.repeat(3).batch(7, drop_remainder=True)
dataset = dataset.apply(tf.data.experimental.unbatch())
dataset = dataset.filter(lambda x: x<10)
for item in dataset:
    print(item)

tf.Tensor(0, shape=(), dtype=int32)
tf.Tensor(1, shape=(), dtype=int32)
tf.Tensor(2, shape=(), dtype=int32)
tf.Tensor(3, shape=(), dtype=int32)
tf.Tensor(4, shape=(), dtype=int32)
tf.Tensor(5, shape=(), dtype=int32)
tf.Tensor(6, shape=(), dtype=int32)
tf.Tensor(7, shape=(), dtype=int32)
tf.Tensor(8, shape=(), dtype=int32)
tf.Tensor(9, shape=(), dtype=int32)
tf.Tensor(0, shape=(), dtype=int32)
tf.Tensor(1, shape=(), dtype=int32)
tf.Tensor(2, shape=(), dtype=int32)
tf.Tensor(3, shape=(), dtype=int32)
tf.Tensor(4, shape=(), dtype=int32)
tf.Tensor(5, shape=(), dtype=int32)
tf.Tensor(6, shape=(), dtype=int32)
tf.Tensor(7, shape=(), dtype=int32)
tf.Tensor(8, shape=(), dtype=int32)
tf.Tensor(9, shape=(), dtype=int32)
tf.Tensor(0, shape=(), dtype=int32)
tf.Tensor(1, shape=(), dtype=int32)
tf.Tensor(2, shape=(), dtype=int32)
tf.Tensor(3, shape=(), dtype=int32)
tf.Tensor(4, shape=(), dtype=int32)
tf.Tensor(5, shape=(), dtype=int32)
tf.Tensor(6, shape=(), dtype=int32)
tf.Tensor(7, shape=(), dtype

In [9]:
dataset = tf.data.Dataset.from_tensor_slices(X)
dataset = dataset.repeat(3).batch(7, drop_remainder=True)
dataset = dataset.filter(lambda x: len(x)<5)
for item in dataset:
    print(item)

> **filter** 메서드를 이용하여 데이터셋을 필터링할 수도 있음.

In [11]:
dataset = tf.data.Dataset.from_tensor_slices(X)
dataset = dataset.repeat(3).batch(7, drop_remainder=True)
for item in dataset.take(2):
    print(item)

tf.Tensor([0 1 2 3 4 5 6], shape=(7,), dtype=int32)
tf.Tensor([7 8 9 0 1 2 3], shape=(7,), dtype=int32)


> **take** 메서드를 사용하여 데이터셋에 있는 몇 개의 아이템만 뽑아서 볼 수 있음.

---
## 데이터 셔플링
경사 하강법은 학습 데이터셋에 있는 샘플이 **독립적이고 동일한 분포일 때** 최고의 성능을 발휘함.  
이렇게 하는 간단한 방법은 **shuffle()** 메서드를 사용하여 샘플을 섞는 것.  
1. shuffle메서드는 먼저 원본 데이터셋의 처음 아이템을 **buffer_size**만큼 추출하여 버퍼에 채움.  
2. 그 다음 새로운 아이템이 요청되면 이 버퍼에서 랜덤하게 하나를 꺼내 반환함. 
3. 그리고 원본 데이터셋에서 새로운 아이템을 추출하여 비워진 버퍼를 채움.
4. 원본 데이터셋의 모든 아이템이 사용될 때까지 반복.
5. 그 다음엔 버퍼가 비워질 때까지 계속하여 랜덤하게 아이템을 반환.

이 메서드를 사용하려면 버퍼 크기를 지정해야 함.  
버퍼 크기는 충분히 크게 하는 것이 중요. 그렇지 않으면 셔플링의 효과가 감소된다고 함.(다만 보유한 메모리 크기는 넘지 않아야 함, 데이터셋 크기도 넘을 필요 없음.)  

In [13]:
dataset = tf.data.Dataset.range(10).repeat(3)
for item in dataset:
    print(item)

tf.Tensor(0, shape=(), dtype=int64)
tf.Tensor(1, shape=(), dtype=int64)
tf.Tensor(2, shape=(), dtype=int64)
tf.Tensor(3, shape=(), dtype=int64)
tf.Tensor(4, shape=(), dtype=int64)
tf.Tensor(5, shape=(), dtype=int64)
tf.Tensor(6, shape=(), dtype=int64)
tf.Tensor(7, shape=(), dtype=int64)
tf.Tensor(8, shape=(), dtype=int64)
tf.Tensor(9, shape=(), dtype=int64)
tf.Tensor(0, shape=(), dtype=int64)
tf.Tensor(1, shape=(), dtype=int64)
tf.Tensor(2, shape=(), dtype=int64)
tf.Tensor(3, shape=(), dtype=int64)
tf.Tensor(4, shape=(), dtype=int64)
tf.Tensor(5, shape=(), dtype=int64)
tf.Tensor(6, shape=(), dtype=int64)
tf.Tensor(7, shape=(), dtype=int64)
tf.Tensor(8, shape=(), dtype=int64)
tf.Tensor(9, shape=(), dtype=int64)
tf.Tensor(0, shape=(), dtype=int64)
tf.Tensor(1, shape=(), dtype=int64)
tf.Tensor(2, shape=(), dtype=int64)
tf.Tensor(3, shape=(), dtype=int64)
tf.Tensor(4, shape=(), dtype=int64)
tf.Tensor(5, shape=(), dtype=int64)
tf.Tensor(6, shape=(), dtype=int64)
tf.Tensor(7, shape=(), dtype

In [15]:
dataset = tf.data.Dataset.range(10).repeat(3)
dataset = dataset.shuffle(buffer_size=1, seed=42)
for item in dataset:
    print(item)

tf.Tensor(0, shape=(), dtype=int64)
tf.Tensor(1, shape=(), dtype=int64)
tf.Tensor(2, shape=(), dtype=int64)
tf.Tensor(3, shape=(), dtype=int64)
tf.Tensor(4, shape=(), dtype=int64)
tf.Tensor(5, shape=(), dtype=int64)
tf.Tensor(6, shape=(), dtype=int64)
tf.Tensor(7, shape=(), dtype=int64)
tf.Tensor(8, shape=(), dtype=int64)
tf.Tensor(9, shape=(), dtype=int64)
tf.Tensor(0, shape=(), dtype=int64)
tf.Tensor(1, shape=(), dtype=int64)
tf.Tensor(2, shape=(), dtype=int64)
tf.Tensor(3, shape=(), dtype=int64)
tf.Tensor(4, shape=(), dtype=int64)
tf.Tensor(5, shape=(), dtype=int64)
tf.Tensor(6, shape=(), dtype=int64)
tf.Tensor(7, shape=(), dtype=int64)
tf.Tensor(8, shape=(), dtype=int64)
tf.Tensor(9, shape=(), dtype=int64)
tf.Tensor(0, shape=(), dtype=int64)
tf.Tensor(1, shape=(), dtype=int64)
tf.Tensor(2, shape=(), dtype=int64)
tf.Tensor(3, shape=(), dtype=int64)
tf.Tensor(4, shape=(), dtype=int64)
tf.Tensor(5, shape=(), dtype=int64)
tf.Tensor(6, shape=(), dtype=int64)
tf.Tensor(7, shape=(), dtype

>**buffer_size** 의 크기를 1로 하니 셔플의 의미가 없어짐

In [16]:
dataset = tf.data.Dataset.range(10).repeat(3)
dataset = dataset.shuffle(buffer_size=10, seed=42).batch(7)
for item in dataset:
    print(item)

tf.Tensor([5 2 8 1 7 9 2], shape=(7,), dtype=int64)
tf.Tensor([0 0 4 6 3 1 0], shape=(7,), dtype=int64)
tf.Tensor([9 3 7 6 7 8 3], shape=(7,), dtype=int64)
tf.Tensor([4 6 8 4 1 5 9], shape=(7,), dtype=int64)
tf.Tensor([5 2], shape=(2,), dtype=int64)


---
메모리 용량보다 큰 대규모 데이터셋은 버퍼가 데이터셋에 비해 작기 때문에 간단한 셔플링 버퍼 방식으로는 충분하지 않음.  
이를 해결하는 방법은 **원본 데이터 자체를 섞는 것**. 그러면 셔플링 효과가 크게 향상됨.  
원본 데이터가 섞여 있더라도 일반적으로 에포크마다 한번 더 섞음. 그렇지 않으면 에포크마다 동일한 순서가 반복되어 모델에 편향이 추가됨.  
샘플을 더 섞기 위해 많이 사용하는 방법은 원본 데이터를 여러 파일로 나눈 다음 학습하는 동안 무작위로 읽는 것. 하지만 동일한 파일에 있는 샘플은 여전히 함께 처리함. 이를 피하기 위해서는 파일 여러 개를 무작위로 선택하고 파일에서 동시에 읽은 레코드를 돌아가면서 반환할 수 있음. 그 다음에 shuffle()메서드를 사용해 그 위에 셔플링 버퍼를 추가할 수 있음.  
복잡하게 보이지만 데이터 API를 사용해 몇 줄의 코드로 구현 가능하다고 함.

## 여러 파일에서 한 줄씩 번갈아 읽기
캘리포니아 주택 데이터셋을 적재하고 섞은 다음 학습셋, 검증셋, 테스트셋으로 나누었다고 가정. 그 다음 각 세트를 csv파일 여러 개로 나눔.  
(각 행은 8개의 입력 특성과 타깃인 중간 주택 가격을 담고 있음)

In [17]:
from sklearn.datasets import fetch_california_housing
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

housing = fetch_california_housing()
X_train_full, X_test, y_train_full, y_test = train_test_split(
    housing.data, housing.target.reshape(-1, 1), random_state=42)
X_train, X_valid, y_train, y_valid = train_test_split(
    X_train_full, y_train_full, random_state=42)

scaler = StandardScaler()
scaler.fit(X_train)
X_mean = scaler.mean_
X_std = scaler.scale_

In [18]:
def save_to_multiple_csv_files(data, name_prefix, header=None, n_parts=10):
    housing_dir = os.path.join("datasets", "housing")
    os.makedirs(housing_dir, exist_ok=True)
    path_format = os.path.join(housing_dir, "my_{}_{:02d}.csv")

    filepaths = []
    m = len(data)
    for file_idx, row_indices in enumerate(np.array_split(np.arange(m), n_parts)):
        part_csv = path_format.format(name_prefix, file_idx)
        filepaths.append(part_csv)
        with open(part_csv, "wt", encoding="utf-8") as f:
            if header is not None:
                f.write(header)
                f.write("\n")
            for row_idx in row_indices:
                f.write(",".join([repr(col) for col in data[row_idx]]))
                f.write("\n")
    return filepaths

In [21]:
import numpy as np
import os

train_data = np.c_[X_train, y_train]
valid_data = np.c_[X_valid, y_valid]
test_data = np.c_[X_test, y_test]
header_cols = housing.feature_names + ["MedianHouseValue"]
header = ",".join(header_cols)

train_filepaths = save_to_multiple_csv_files(train_data, "train", header, n_parts=20)
valid_filepaths = save_to_multiple_csv_files(valid_data, "valid", header, n_parts=10)
test_filepaths = save_to_multiple_csv_files(test_data, "test", header, n_parts=10)

In [23]:
import pandas as pd

pd.read_csv(train_filepaths[0]).head(10)

MedInc  HouseAge   AveRooms  AveBedrms  Population  AveOccup  Latitude  \
0  3.5214      15.0   3.049945   1.106548      1447.0  1.605993     37.63   
1  5.3275       5.0   6.490060   0.991054      3464.0  3.443340     33.69   
2  3.1000      29.0   7.542373   1.591525      1328.0  2.250847     38.44   
3  7.1736      12.0   6.289003   0.997442      1054.0  2.695652     33.55   
4  2.0549      13.0   5.312457   1.085092      3297.0  2.244384     33.93   
5  2.9583      50.0   5.380282   1.117371       579.0  2.718310     33.98   
6  3.5200      23.0   4.698217   1.034294      2202.0  3.020576     34.14   
7  2.7188      32.0   5.511628   1.067829      1337.0  2.591085     34.94   
8  2.6563      26.0   4.294893   1.123558      1401.0  2.308072     37.68   
9  1.6944      11.0  21.372093   4.627907        69.0  1.604651     40.19   

   Longitude  MedianHouseValue  
0    -122.43             1.442  
1    -117.39             1.687  
2    -122.98             1.621  
3    -117.70             2.621  
4    -116.93             0.956  
5    -118.06             1.726  
6    -118.01             1.873  
7    -120.42             1.337  
8    -122.08             1.841  
9    -121.08             1.375

In [26]:
filepath_dataset = tf.data.Dataset.list_files(train_filepaths, seed=42)
for item in filepath_dataset:
    print(item)

tf.Tensor(b'datasets\\housing\\my_train_05.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_16.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_01.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_17.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_00.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_14.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_10.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_02.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_12.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_19.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_07.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_09.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_13.csv', shape=(), dtype=string)
tf.Tensor(b'datasets\\housing\\my_train_15.csv', sh

**list_files()** 함수는 파일 경로를 섞은 데이터셋을 반환함.  
일반적으로 이는 바람직한 설정이지만 어떤 이유로 이를 원하지 않으면 **shuffle=False**로 설정할 수 있음.

In [34]:
n_readers = 5
dataset = filepath_dataset.interleave(
lambda filepath: tf.data.TextLineDataset(filepath).skip(1),
cycle_length=n_readers)
for item in dataset:
    print("\n---")
    print(item)


---
tf.Tensor(b'3.3456,37.0,4.514084507042254,0.9084507042253521,458.0,3.2253521126760565,36.67,-121.7,2.526', shape=(), dtype=string)

---
tf.Tensor(b'3.6641,17.0,5.577142857142857,1.1542857142857144,511.0,2.92,40.85,-121.07,0.808', shape=(), dtype=string)

---
tf.Tensor(b'3.5214,15.0,3.0499445061043287,1.106548279689234,1447.0,1.6059933407325193,37.63,-122.43,1.442', shape=(), dtype=string)

---
tf.Tensor(b'2.4792,24.0,3.4547038327526134,1.1341463414634145,2251.0,3.921602787456446,34.18,-118.38,2.0', shape=(), dtype=string)

---
tf.Tensor(b'1.6571,34.0,4.454976303317536,1.0876777251184835,1358.0,3.2180094786729856,37.94,-122.35,1.052', shape=(), dtype=string)

---
tf.Tensor(b'2.233,25.0,4.746987951807229,1.1325301204819278,155.0,1.8674698795180722,38.58,-121.22,0.55', shape=(), dtype=string)

---
tf.Tensor(b'3.5795,12.0,6.857575757575757,1.2424242424242424,913.0,2.7666666666666666,37.47,-121.11,1.456', shape=(), dtype=string)

---
tf.Tensor(b'5.3275,5.0,6.490059642147117,0.991053677

---
tf.Tensor(b'2.9726,9.0,3.603448275862069,1.0496957403651115,2017.0,2.0456389452332657,33.78,-117.95,1.338', shape=(), dtype=string)

---
tf.Tensor(b'5.9546,39.0,5.669064748201439,0.920863309352518,413.0,2.971223021582734,34.13,-118.08,3.967', shape=(), dtype=string)

---
tf.Tensor(b'2.7361,14.0,4.206611570247934,0.9834710743801653,1224.0,3.371900826446281,32.57,-117.07,0.936', shape=(), dtype=string)

---
tf.Tensor(b'2.7538,41.0,4.376731301939058,1.0664819944598338,881.0,2.440443213296399,37.64,-120.99,0.996', shape=(), dtype=string)

---
tf.Tensor(b'2.4408,32.0,4.457207207207207,1.1058558558558558,954.0,2.1486486486486487,33.95,-117.4,1.173', shape=(), dtype=string)

---
tf.Tensor(b'4.9097,17.0,5.365853658536586,1.048780487804878,431.0,3.5040650406504064,37.28,-121.76,2.41', shape=(), dtype=string)

---
tf.Tensor(b'3.8417,11.0,6.667844522968198,1.0706713780918728,775.0,2.7385159010600706,39.03,-121.06,1.872', shape=(), dtype=string)

---
tf.Tensor(b'3.0313,43.0,4.620052770448549,1


---
tf.Tensor(b'9.8074,16.0,8.789823008849558,1.0685840707964602,1373.0,3.0376106194690267,33.8,-117.77,4.17', shape=(), dtype=string)

---
tf.Tensor(b'2.2813,22.0,3.8558823529411765,0.9382352941176471,1455.0,4.279411764705882,37.38,-120.72,0.673', shape=(), dtype=string)

---
tf.Tensor(b'2.9526,24.0,4.725085910652921,1.168384879725086,1699.0,1.9461626575028637,37.9,-122.05,2.71', shape=(), dtype=string)

---
tf.Tensor(b'3.6523,19.0,5.794819359236537,1.0620313565098842,3576.0,2.4376278118609407,38.64,-121.32,1.585', shape=(), dtype=string)

---
tf.Tensor(b'2.4107,38.0,5.36231884057971,1.181159420289855,332.0,2.4057971014492754,34.15,-117.3,0.88', shape=(), dtype=string)

---
tf.Tensor(b'2.101,21.0,4.413793103448276,0.9396551724137931,890.0,3.836206896551724,33.12,-115.51,0.467', shape=(), dtype=string)

---
tf.Tensor(b'4.7639,49.0,5.304964539007092,1.044917257683215,1948.0,4.6052009456264775,37.71,-122.45,2.515', shape=(), dtype=string)

---
tf.Tensor(b'3.775,52.0,4.3979591836734695,0


---
tf.Tensor(b'2.5726,41.0,3.8424015009380863,1.127579737335835,852.0,1.598499061913696,33.77,-118.18,1.938', shape=(), dtype=string)

---
tf.Tensor(b'3.1607,52.0,4.313679245283019,1.1132075471698113,779.0,1.8372641509433962,33.99,-118.45,3.39', shape=(), dtype=string)

---
tf.Tensor(b'7.6245,21.0,6.663822525597269,0.9948805460750854,1528.0,2.6075085324232083,36.55,-121.7,3.366', shape=(), dtype=string)

---
tf.Tensor(b'3.6042,21.0,5.619883040935672,1.0058479532163742,1051.0,3.073099415204678,38.33,-122.31,1.833', shape=(), dtype=string)

---
tf.Tensor(b'5.0853,26.0,5.916496945010183,1.0264765784114054,1452.0,2.9572301425661913,33.68,-117.89,2.603', shape=(), dtype=string)

---
tf.Tensor(b'1.5771,12.0,4.175903614457831,1.0144578313253012,1861.0,4.48433734939759,39.53,-121.56,0.652', shape=(), dtype=string)

---
tf.Tensor(b'3.4219,32.0,5.228228228228228,1.12012012012012,872.0,2.6186186186186187,34.13,-117.87,1.945', shape=(), dtype=string)

---
tf.Tensor(b'4.9821,21.0,4.48756756756756


---
tf.Tensor(b'1.4729,32.0,4.4541176470588235,1.0658823529411765,1744.0,4.103529411764706,36.34,-119.31,0.541', shape=(), dtype=string)

---
tf.Tensor(b'2.9243,35.0,5.745819397993311,1.1538461538461537,698.0,2.3344481605351173,39.46,-123.8,1.316', shape=(), dtype=string)

---
tf.Tensor(b'4.9102,37.0,5.070621468926554,0.9774011299435028,1082.0,3.056497175141243,34.2,-118.52,2.072', shape=(), dtype=string)

---
tf.Tensor(b'2.8981,26.0,3.0994318181818183,1.0,1638.0,2.3267045454545454,37.31,-121.93,2.298', shape=(), dtype=string)

---
tf.Tensor(b'2.3333,47.0,4.76878612716763,1.0809248554913296,416.0,2.4046242774566475,34.0,-118.33,1.333', shape=(), dtype=string)

---
tf.Tensor(b'8.3634,14.0,7.475778546712803,1.0069204152249136,2025.0,3.5034602076124566,33.71,-117.76,3.551', shape=(), dtype=string)

---
tf.Tensor(b'3.0806,52.0,6.1931034482758625,1.0413793103448277,1152.0,2.6482758620689655,40.54,-124.23,1.067', shape=(), dtype=string)

---
tf.Tensor(b'4.0791,11.0,5.8789020452099034,1.0984

...


---
tf.Tensor(b'4.5791,12.0,5.8992673992674,1.021978021978022,2966.0,2.7161172161172162,35.36,-119.08,1.234', shape=(), dtype=string)

---
tf.Tensor(b'2.1974,51.0,4.23489932885906,1.0369127516778522,608.0,2.040268456375839,38.01,-122.13,1.393', shape=(), dtype=string)

---
tf.Tensor(b'2.181,37.0,4.6773255813953485,1.0872093023255813,1173.0,3.4098837209302326,36.71,-119.56,0.599', shape=(), dtype=string)

---
tf.Tensor(b'5.01,20.0,17.54609929078014,4.432624113475177,338.0,2.397163120567376,37.65,-118.99,1.955', shape=(), dtype=string)

---
tf.Tensor(b'4.525,30.0,5.184049079754601,1.107361963190184,2269.0,3.4800613496932513,33.75,-118.01,1.86', shape=(), dtype=string)

---
tf.Tensor(b'2.7543,23.0,3.2066666666666666,1.1577777777777778,1264.0,2.8088888888888888,34.08,-118.31,2.2', shape=(), dtype=string)

---
tf.Tensor(b'6.155,16.0,6.998316498316498,0.9865319865319865,2036.0,3.4276094276094278,33.92,-117.58,2.464', shape=(), dtype=string)

---
tf.Tensor(b'3.8846,39.0,4.8301158301158305,1.


---
tf.Tensor(b'2.3774,26.0,4.867803837953092,1.0788912579957357,634.0,1.35181236673774,33.6,-117.7,0.743', shape=(), dtype=string)

---
tf.Tensor(b'4.1303,16.0,3.3026444662095984,1.078354554358472,2049.0,2.006856023506366,37.67,-122.46,1.465', shape=(), dtype=string)

---
tf.Tensor(b'3.375,33.0,3.732456140350877,1.013157894736842,936.0,4.105263157894737,34.08,-118.17,1.475', shape=(), dtype=string)

---
tf.Tensor(b'0.7445,19.0,3.5675675675675675,1.045045045045045,641.0,2.8873873873873874,36.33,-119.29,1.125', shape=(), dtype=string)

---
tf.Tensor(b'2.455,42.0,5.223076923076923,1.1205128205128205,2736.0,3.5076923076923077,37.73,-122.18,0.824', shape=(), dtype=string)

---
tf.Tensor(b'3.5375,35.0,6.543956043956044,1.043956043956044,537.0,2.9505494505494507,36.74,-119.85,0.967', shape=(), dtype=string)

---
tf.Tensor(b'7.167,20.0,7.72865275142315,1.073055028462998,3562.0,3.379506641366224,34.26,-118.59,3.571', shape=(), dtype=string)

---
tf.Tensor(b'5.1057,45.0,5.381578947368421,0.967

tf.Tensor(b'4.1656,24.0,4.687951807228916,1.0433734939759036,1568.0,1.889156626506024,34.15,-118.41,3.647', shape=(), dtype=string)

---
tf.Tensor(b'6.1885,10.0,6.631578947368421,0.9818511796733213,1638.0,2.972776769509982,34.26,-119.17,2.673', shape=(), dtype=string)

---
tf.Tensor(b'6.0336,10.0,6.26032315978456,0.9784560143626571,1410.0,2.5314183123877916,33.11,-117.24,2.403', shape=(), dtype=string)

---
tf.Tensor(b'1.975,35.0,4.699346405228758,1.088235294117647,794.0,2.5947712418300655,34.03,-118.35,1.381', shape=(), dtype=string)

---
tf.Tensor(b'2.6613,26.0,5.19,1.0033333333333334,986.0,3.2866666666666666,38.49,-121.49,0.777', shape=(), dtype=string)

---
tf.Tensor(b'4.8438,22.0,5.490312965722802,1.018628912071535,4721.0,3.5178837555886737,33.83,-118.24,2.131', shape=(), dtype=string)

---
tf.Tensor(b'6.448,30.0,6.641025641025641,0.967948717948718,467.0,2.9935897435897436,37.34,-122.02,3.606', shape=(), dtype=string)

---
tf.Tensor(b'2.7159,44.0,5.1054545454545455,1.0636363636363


---
tf.Tensor(b'3.1719,39.0,5.759075907590759,1.0594059405940595,901.0,2.9735973597359737,36.75,-119.73,0.679', shape=(), dtype=string)

---
tf.Tensor(b'3.6413,40.0,4.604735883424408,1.041894353369763,1318.0,2.400728597449909,34.27,-119.26,2.127', shape=(), dtype=string)

---
tf.Tensor(b'1.4524,42.0,3.5231316725978647,1.0284697508896796,1167.0,4.153024911032029,34.01,-118.27,1.268', shape=(), dtype=string)

---
tf.Tensor(b'4.1842,34.0,7.020576131687243,1.1358024691358024,628.0,2.5843621399176953,34.36,-119.71,3.64', shape=(), dtype=string)

---
tf.Tensor(b'6.7181,15.0,7.199438202247191,0.9410112359550562,1080.0,3.033707865168539,36.83,-119.85,1.603', shape=(), dtype=string)

---
tf.Tensor(b'1.7426,33.0,4.993318485523385,1.1514476614699332,1160.0,2.5835189309576836,39.73,-121.82,0.603', shape=(), dtype=string)

---
tf.Tensor(b'5.411,5.0,5.137037037037037,0.8740740740740741,855.0,3.1666666666666665,34.0,-117.66,2.011', shape=(), dtype=string)

---
tf.Tensor(b'1.4375,17.0,2.4814814814814


---
tf.Tensor(b'4.2312,43.0,5.610108303249097,1.036101083032491,802.0,2.895306859205776,34.12,-118.07,2.726', shape=(), dtype=string)

---
tf.Tensor(b'2.8698,23.0,5.475471698113208,1.1018867924528302,1052.0,3.969811320754717,37.38,-120.73,0.729', shape=(), dtype=string)

---
tf.Tensor(b'1.2679,30.0,4.607843137254902,1.0343137254901962,1071.0,5.25,33.94,-118.24,0.92', shape=(), dtype=string)

---
tf.Tensor(b'1.9306,22.0,4.176470588235294,1.326797385620915,664.0,4.339869281045751,33.66,-116.17,0.475', shape=(), dtype=string)

---
tf.Tensor(b'4.8194,45.0,5.197860962566845,0.9679144385026738,554.0,2.962566844919786,34.21,-118.4,1.813', shape=(), dtype=string)

---
tf.Tensor(b'3.5295,15.0,4.567365269461078,1.0254491017964071,1479.0,2.214071856287425,37.68,-122.08,2.422', shape=(), dtype=string)

---
tf.Tensor(b'3.4583,52.0,4.5109289617486334,0.9590163934426229,973.0,2.658469945355191,37.74,-122.42,2.409', shape=(), dtype=string)

---
tf.Tensor(b'4.0938,35.0,5.293532338308458,1.009950248756

**interleave()** 메서드는 filepath_dataset에 있는 다섯 개의 파일 경로에서 읽는 데이터셋을 만듦.(**skip(1)은 해당 파일에서 특성 이름에 해당하는 행을 무시하겠다는 의미임**)  

이 메서드에 전달한 함수를 각 파일에 대해 호출하여 새로운 데이터셋(여기선 TextLineFadataset)을 만듦.  
이 단계에서 총 7개의 데이터셋이 있음.
- 파일 경로 데이터셋
- 인터리브 데이터셋
- 인터리브 데이터셋에 의해 내부적으로 생성된 다섯개의 TextLineDataset



인터리브 데이터셋을 반복 구문에 사용하면
- 다섯 개의 TextLineDataset을 번갈아 가면서 순회함. 
- 모든 데이터셋이 아이템을 소진할 때까지 한 번에 한 줄씩 읽음. 
- 그 후에 filepath_dataset에서 다음 다섯 개의 파일 경로를 가져오고 동일한 방식으로 한 줄씩 읽음. 
- 모든 파일 경로가 소진될 때까지 계속 함.

인터리빙이 잘 동작하려면 파일의 길이가 동일한 것이 좋음. 그렇지 않으면 가장 긴 파일 끝은 인터리빙이 안됨.

In [37]:
for line in dataset.take(5):
    print(line.numpy())

b'3.6875,44.0,4.524475524475524,0.993006993006993,457.0,3.195804195804196,34.04,-118.15,1.625'
b'5.9522,26.0,6.196521739130435,1.0069565217391305,1479.0,2.5721739130434784,34.5,-119.75,4.384'
b'3.6641,17.0,5.577142857142857,1.1542857142857144,511.0,2.92,40.85,-121.07,0.808'
b'4.6477,38.0,5.03728813559322,0.911864406779661,745.0,2.5254237288135593,32.64,-117.07,1.504'
b'4.2083,44.0,5.323204419889502,0.9171270718232044,846.0,2.3370165745856353,37.47,-122.2,2.782'


> 잘 작동된 모습. 하지만 아직 바이트 스트링 형태임.  
**이를 파싱하고 스케일을 조정할 필요가 있음**

---
## 데이터 전처리

In [38]:
x_mean, x_std = X_mean, X_std
n_inputs = 8

def preprocessing(line):
    defs = [0.0] * n_inputs + [tf.constant([], dtype=tf.float32)]
    fields = tf.io.decode_csv(line, record_defaults=defs)
    x = tf.stack(fields[: -1])
    y = tf.stack(fields[-1: ])
    return (x - x_mean) / x_std, y

- 학습 데이터셋으로부터 각 특성의 평균과 표준편차를 미리 게싼했다고 가정.
- preprocessing() 함수는 CSV한 라인을 받아 파싱함. 이를 위해 **tf.io.decode_csv** 함수를 사용. 이 함수는 두 개의 매개변수를 받음. 
    1. 첫 번째로 파싱할 라인
    2. 두 번째로 CSV파일의 각 열에 대한 기본값을 담은 배열.
    이 배열은 텐서플로에게 각 열의 기본값뿐 아니라 열 개수와 데이터 타입도 알려줌. 이 에에서는 모든 특성 열이 실수이고 누락된 값의 기본값은 0으로 지정. 마지막열(타깃값)에는 tf.float32 타입의 빈 배열을 제공. 이 배열은 텐서플로에게 해당 열은 실수이지만 기본값은 없다고 알려줌. 따라서 이 열에서 누락된 값이 발견되면 예외가 발생할 것.
    
- **decode_csv()** 함수는 (열마다 한 개씩) 스칼라 텐서의 리스트를 반환함. 1D 텐서 배열을 반환해야 하므로 마지막 열(타깃)을 제외하고 모든 텐서에 대해 **tf.stack()**함수를 호출함. 이 함수는 모든 텐서를 쌓아 1D 배열을 만듦. 그 다음 타깃값에도 동일하게 적용. 

In [43]:
for line in dataset.take(5):
    print("\n---")
    print(line)
    features, target = preprocessing(line)
    print(features)
    print(target)


---
tf.Tensor(b'3.226,52.0,5.372469635627531,0.9473684210526315,1157.0,2.3421052631578947,37.96,-121.31,1.076', shape=(), dtype=string)
tf.Tensor(
[-0.3486974   1.8491895  -0.03272728 -0.32713076 -0.24392317 -0.2611868
  1.0838584  -0.8624136 ], shape=(8,), dtype=float32)
tf.Tensor([1.076], shape=(1,), dtype=float32)

---
tf.Tensor(b'4.6477,38.0,5.03728813559322,0.911864406779661,745.0,2.5254237288135593,32.64,-117.07,1.504', shape=(), dtype=string)
tf.Tensor(
[ 0.39593136  0.74167496 -0.16415128 -0.40340805 -0.6199179  -0.18355484
 -1.4084505   1.2565969 ], shape=(8,), dtype=float32)
tf.Tensor([1.504], shape=(1,), dtype=float32)

---
tf.Tensor(b'1.6571,34.0,4.454976303317536,1.0876777251184835,1358.0,3.2180094786729856,37.94,-122.35,1.052', shape=(), dtype=string)
tf.Tensor(
[-1.1704237   0.42524222 -0.3924749  -0.02568866 -0.06048884  0.10974211
  1.0744886  -1.3821716 ], shape=(8,), dtype=float32)
tf.Tensor([1.052], shape=(1,), dtype=float32)

---
tf.Tensor(b'4.2083,44.0,5.32320441

---
# 데이터 로드와 전처리 합치기
CSV파일에서 캘리포니아 주택 데이터셋을 효율적으로 적재하고 전처리, 셔플링, 반복, 배치를 적용한 데이터셋을 반환하는 헬퍼 함수 작성

In [72]:
def csv_reader_dataset(filepaths, repeat=1, n_readers=5,
                      n_read_threads=None, shuffle_buffer_size=10000,
                      n_parse_threads=5, batch_size=32,
                      autotune=False):
    
    dataset = tf.data.Dataset.list_files(filepaths).repeat(repeat)
    
    if autotune:
        dataset = dataset.interleave(
            lambda filepath: tf.data.TextLineDataset(filepath).skip(1),
            cycle_length=n_readers, num_parallel_calls=tf.data.experimental.AUTOTUNE)

        dataset = dataset.shuffle(shuffle_buffer_size)
        dataset = dataset.map(preprocessing, num_parallel_calls=tf.data.experimental.AUTOTUNE)
        
    else:
        dataset = dataset.interleave(
            lambda filepath: tf.data.TextLineDataset(filepath).skip(1),
            cycle_length=n_readers, num_parallel_calls=n_read_threads)

        dataset = dataset.shuffle(shuffle_buffer_size)
        dataset = dataset.map(preprocessing, num_parallel_calls=n_parse_threads)
        
    return dataset.batch(batch_size).prefetch(1)

In [76]:
import time

t1 = time.time()
temp_dataset = csv_reader_dataset(train_filepaths, autotune=False)
t2 = time.time()
print(t2 - t1)
for item in temp_dataset:
    print("\n---")
    print(item)

0.0510103702545166

---
(<tf.Tensor: shape=(32, 8), dtype=float32, numpy=
array([[-0.7203571 ,  0.10880951, -0.39207345,  0.3244786 , -0.60622877,
        -0.39476904,  0.44672647, -1.1472806 ],
       [-0.77854687, -0.60316414, -0.20028527,  0.15478584,  0.7407815 ,
         0.42291173,  0.60132545, -1.0973046 ],
       [ 0.14400306,  0.5043504 , -0.20555456, -0.09078687,  0.07366463,
         0.48833945, -0.80411196,  0.77182245],
       [-0.71255314,  0.6625668 , -0.81397116, -0.02069937, -1.0889987 ,
        -0.27478275,  0.46078208, -1.1372869 ],
       [ 1.6829656 , -1.2360295 ,  0.19096066, -0.19873801,  0.7444319 ,
         0.4378808 ,  0.81682545, -1.1472806 ],
       [ 1.8158958 , -0.998705  ,  0.78105205, -0.29611385,  0.48160067,
         0.18210629,  0.938631  , -1.0923059 ],
       [-0.42579484,  1.216324  , -0.3378203 , -0.3169382 , -0.20741881,
         0.17488259, -0.7994279 ,  0.65187943],
       [-0.06827661,  1.8491895 , -0.00616337, -0.1323234 , -0.9119527 ,
      

       [2.351  ]], dtype=float32)>)

---
(<tf.Tensor: shape=(32, 8), dtype=float32, numpy=
array([[-3.82898867e-01, -8.40488672e-01,  1.51311684e+00,
         3.77826786e+00, -9.58495677e-01, -5.92224766e-03,
        -1.20700431e+00,  2.30110788e+00],
       [-6.19847655e-01,  1.37454045e+00, -5.20190954e-01,
        -3.09054345e-01, -6.60072684e-01, -2.43295372e-01,
        -7.29155362e-01,  9.66731191e-01],
       [-1.14402628e+00, -1.55246222e+00, -2.03413978e-01,
         2.06889242e-01,  5.44998460e-02, -9.13864300e-02,
         2.31226504e-01, -3.82637829e-01],
       [-9.85798538e-01,  7.41674960e-01, -3.95997137e-01,
        -1.19411582e-02, -4.28270102e-01,  1.56120315e-01,
         8.44934821e-01, -1.26722729e+00],
       [ 1.96935737e+00, -1.39424586e+00,  5.73916852e-01,
        -1.87680945e-01,  7.86411941e-01, -1.72580063e-01,
         1.00890183e+00, -1.21724761e+00],
       [ 1.08760822e+00,  3.46134037e-01,  2.57626027e-01,
        -9.52741802e-02, -2.97767073e-01, -1.

       [1.508  ]], dtype=float32)>)

---
(<tf.Tensor: shape=(32, 8), dtype=float32, numpy=
array([[-4.35536772e-01,  2.97013279e-02,  3.09865713e-01,
         4.20701414e-01, -6.87450945e-01, -1.76676244e-01,
        -2.09143236e-01, -1.72736660e-01],
       [-1.01797156e-01,  5.83458602e-01, -3.94571535e-02,
        -1.41521618e-01,  4.36882854e-01,  4.26101759e-02,
        -1.36628723e+00,  1.25159812e+00],
       [ 1.62020385e-01, -1.55246222e+00,  2.31034055e-01,
        -1.30892262e-01,  4.84338492e-01,  8.23074877e-02,
         2.68705696e-01,  1.27122715e-01],
       [ 8.13000977e-01,  6.62566781e-01,  1.83048591e-01,
        -2.22351551e-01, -6.14442229e-01, -2.50924136e-02,
        -7.71318555e-01,  5.91906071e-01],
       [-1.77899495e-01,  5.04350424e-01,  3.22242558e-01,
         3.46023403e-02, -7.33994007e-01, -3.74764688e-02,
         1.30872822e+00, -1.55209434e+00],
       [ 2.15705708e-01,  1.84918952e+00,  1.20529808e-01,
        -7.79903010e-02, -4.87589657e-01,  3.

       [1.535  ]], dtype=float32)>)

---
(<tf.Tensor: shape=(32, 8), dtype=float32, numpy=
array([[ 2.41212979e-01, -9.19596851e-01,  4.80385482e-01,
        -9.56401676e-02, -4.68424886e-01,  2.65839219e-01,
        -1.24448168e+00,  2.02123952e+00],
       [ 4.12115514e-01, -9.98705029e-01, -4.15134169e-02,
        -2.47228723e-02,  1.00908840e+00,  5.83678000e-02,
         9.10521626e-01, -1.22224629e+00],
       [-8.15524220e-01,  2.97013279e-02, -7.09612668e-01,
        -1.09390229e-01, -3.35184038e-01, -1.05281740e-01,
        -8.55644941e-01,  8.21798384e-01],
       [ 1.37515223e+00, -3.65839571e-01,  3.90802443e-01,
        -2.25363910e-01,  1.18382446e-01, -9.84808877e-02,
        -5.60502589e-01, -1.12763256e-01],
       [ 6.85816705e-02, -7.61380494e-01,  1.93793774e-01,
        -1.90273300e-01,  3.06379825e-01,  1.22117475e-01,
         5.26368856e-01,  2.18098937e-03],
       [-8.03425431e-01,  9.78999496e-01, -1.32559639e-04,
        -1.97466418e-01, -3.23320121e-01,  4.


---
(<tf.Tensor: shape=(32, 8), dtype=float32, numpy=
array([[-0.2590822 , -0.52405596, -0.30567506,  0.19601376, -0.6637231 ,
        -0.02826758, -0.8181658 ,  0.6168959 ],
       [-0.17947078,  0.9789995 , -0.40498242, -0.3049508 , -0.63451964,
        -0.06564824,  0.7980858 , -1.1972603 ],
       [-0.9195953 , -1.6315705 , -0.52929384, -0.1474662 ,  0.23884678,
        -0.0882783 , -1.3288081 ,  1.3215653 ],
       [ 0.6363895 ,  0.5043504 ,  0.03065755, -0.22680672, -0.31966966,
         0.09658626, -0.65419877,  0.5519238 ],
       [ 0.65933007, -0.60316414, -0.01025196, -0.15484834,  2.0184336 ,
        -0.2426715 ,  0.7887178 , -1.1922616 ],
       [-0.60596806,  1.8491895 , -0.54292184, -0.21856047, -0.04497449,
        -0.03229763, -0.71510154,  0.6618731 ],
       [-1.6125292 , -1.3151377 , -0.26460436,  1.2930384 , -1.0123396 ,
        -0.58935964, -1.1835806 ,  1.2416046 ],
       [ 2.1567059 ,  1.8491895 ,  0.31236154, -0.2140565 , -0.8407692 ,
        -0.15502928, -0.7

마지막 줄에 있는 **prefetch(1)** 을 사용하면
> 데이터셋은 항상 한 배치가 미리 준비되도록 최선을 다함(??)  
다시 말하면 학습 알고리즘이 한 배치로 작업을 하는 동안 이 데이터셋이 동시에 다음 배치를 준비한다고 함.  
**이렇게 하면 사용하지 않을 때보다 속도를 향상시켜준다고 함**

파일을 읽을 때나 전처리할 때 순서대로 작업하는 것이 아니라 **병렬로 작업하고 싶다면**
> **num_parallel_calls** 매개변수에서 사용할 스레드 수를 입력하는 것으로 CPU의 멀티 코어를 이용해 구현할 수 있음.
이 매개변수를 **tf.data.experimential.AUTOTUNE** 으로 지정하면 텐서플로가 가용한 CPU를 기반으로 동적으로 적절한 스레드 개수를 선택해준다고 함!

> 일단 병렬 작업을 한 것과 안 한 것을 비교했을 때 데이터셋이 적어서 그런지 아직 큰 차이는 없음.

> 데이터셋이 메모리에 모두 들어갈 수 있을 정도로 작다면 RAM에 모두 캐싱할 수 있는 **cache()** 메서드를 사용하여 학습 속도를 크게 높일 수 있다고 함.

일반적으로 데이터를 적재, 전처리한 후 셔플링, 반복, 배치, 프리페치하기 전에 캐싱을 수행함.

---
## 데이터셋을 tf.keras와 사용하기


In [78]:
train_set = csv_reader_dataset(train_filepaths)
valid_set = csv_reader_dataset(valid_filepaths)
test_set = csv_reader_dataset(test_filepaths)

In [80]:
train_set.element_spec

(TensorSpec(shape=(None, 8), dtype=tf.float32, name=None),
 TensorSpec(shape=(None, 1), dtype=tf.float32, name=None))

In [85]:
tf.data.experimental.cardinality(train_set)

<tf.Tensor: shape=(), dtype=int64, numpy=-2>

In [87]:
keras.backend.clear_session()
np.random.seed(42)
tf.random.set_seed(42)

model = keras.models.Sequential([
    keras.layers.Dense(30, activation="relu", input_shape=X_train.shape[1:]),
    keras.layers.Dense(1),
])

In [88]:
model.compile(loss="mse", optimizer=keras.optimizers.SGD(lr=1e-3))

In [100]:
batch_size = 32

model.fit(train_set, epochs=10, validation_data=valid_set)

Epoch 1/10
363/363 [==============================] - 0s 625us/step - loss: 0.4034 - val_loss: 0.3756
Epoch 2/10
363/363 [==============================] - 0s 587us/step - loss: 0.4018 - val_loss: 0.3787
Epoch 3/10
363/363 [==============================] - 0s 557us/step - loss: 0.4003 - val_loss: 0.3729
Epoch 4/10
363/363 [==============================] - 0s 546us/step - loss: 0.3992 - val_loss: 0.3714
Epoch 5/10
363/363 [==============================] - 0s 562us/step - loss: 0.3975 - val_loss: 0.3697
Epoch 6/10
363/363 [==============================] - 0s 551us/step - loss: 0.3967 - val_loss: 0.3750
Epoch 7/10
363/363 [==============================] - 0s 551us/step - loss: 0.3954 - val_loss: 0.3694
Epoch 8/10
363/363 [==============================] - 0s 551us/step - loss: 0.3943 - val_loss: 0.3671
Epoch 9/10
363/363 [==============================] - 0s 562us/step - loss: 0.3931 - val_loss: 0.3678
Epoch 10/10
363/363 [==============================] - 0s 557us/step - loss: 0.392

In [95]:
model.evaluate(test_set)

162/162 [==============================] - 0s 389us/step - loss: 0.4780


0.4780231714248657

In [96]:
model.predict(test_set)

array([[3.0921643],
       [2.2797942],
       [1.354698 ],
       ...,
       [1.6442786],
       [2.5507693],
       [1.2667198]], dtype=float32)

test셋에는 x데이터와 y데이터 모두 있지만 **predict** 메서드는 y데이터는 알아서 무시해줌

---
> 이제 데이터 API를 사용해 강력한 입력 파이프라인을 만드는 방법을 배웠음.  
하지만 아직까지 CSV파일같은 간단한 예시에 대해서만 다룸.

> 대규모의 복잡한 데이터(이미지나 오디오같은) 구조를 지원하진 못함.  
그래서 **TFRecord** 를 사용하는 방법을 알아야 됨